In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *
import pandas as pd
import re

In [0]:
service_credential = dbutils.secrets.get(scope="<scope>",key="<service-credential-key>")

spark.conf.set("fs.azure.account.auth.type.<storage-account>.dfs.core.windows.net", "OAuth")
spark.conf.set("fs.azure.account.oauth.provider.type.<storage-account>.dfs.core.windows.net", "org.apache.hadoop.fs.azurebfs.oauth2.ClientCredsTokenProvider")
spark.conf.set("fs.azure.account.oauth2.client.id.<storage-account>.dfs.core.windows.net", "<application-id>")
spark.conf.set("fs.azure.account.oauth2.client.secret.<storage-account>.dfs.core.windows.net", service_credential)
spark.conf.set("fs.azure.account.oauth2.client.endpoint.<storage-account>.dfs.core.windows.net", "https://login.microsoftonline.com/<directory-id>/oauth2/token")

In [0]:
#load data to the dataframe
movies_df = spark.read.format('csv')\
        .option("header", True )\
        .option("inferSchema", True )\
        .load('abfss://bronze@movierecommendation2025.dfs.core.windows.net/movies.csv')

In [0]:
#display the dataframe
movies_df.display()

movieId title genres 1 Toy Story (1995) Adventure|Animation|Children|Comedy|Fantasy 2 Jumanji (1995) Adventure|Children|Fantasy 3 Grumpier Old Men (1995) Comedy|Romance 4 Waiting to Exhale (1995) Comedy|Drama|Romance 5 Father of the Bride Part II (1995) Comedy 6 Heat (1995) Action|Crime|Thriller 7 Sabrina (1995) Comedy|Romance 8 Tom and Huck (1995) Adventure|Children 9 Sudden Death (1995) Action 10 GoldenEye (1995) Action|Adventure|Thriller 11 American President, The (1995) Comedy|Drama|Romance 12 Dracula: Dead and Loving It (1995) Comedy|Horror 13 Balto (1995) Adventure|Animation|Children 14 Nixon (1995) Drama 15 Cutthroat Island (1995) Action|Adventure|Romance 16 Casino (1995) Crime|Drama 17 Sense and Sensibility (1995) Drama|Romance 18 Four Rooms (1995) Comedy 19 Ace Ventura: When Nature Calls (1995) Comedy 20 Money Train (1995) Action|Comedy|Crime|Drama|Thriller 21 Get Shorty (1995) Comedy|Crime|Thriller 22 Copycat (1995) Crime|Drama|Horror|Mystery|Thriller 23 Assassins (1995) Action|Crime|Thriller 24 Powder (1995) Drama|Sci-Fi 25 Leaving Las Vegas (1995) Drama|Romance 26 Othello (1995) Drama 27 Now and Then (1995) Children|Drama 28 Persuasion (1995) Drama|Romance 29 City of Lost Children, The (Cité des enfants perdus, La) (1995) Adventure|Drama|Fantasy|Mystery|Sci-Fi 30 Shanghai Triad (Yao a yao yao dao waipo qiao) (1995) Crime|Drama 31 Dangerous Minds (1995) Drama 32 Twelve Monkeys (a.k.a. 12 Monkeys) (1995) Mystery|Sci-Fi|Thriller 33 Wings of Courage (1995) Adventure|Romance|IMAX 34 Babe (1995) Children|Drama 35 Carrington (1995) Drama|Romance 36 Dead Man Walking (1995) Crime|Drama 37 Across the Sea of Time (1995) Documentary|IMAX 38 It Takes Two (1995) Children|Comedy 39 Clueless (1995) Comedy|Romance 40 Cry, the Beloved Country (1995) Drama 41 Richard III (1995) Drama|War 42 Dead Presidents (1995) Action|Crime|Drama 43 Restoration (1995) Drama 44 Mortal Kombat (1995) Action|Adventure|Fantasy 45 To Die For (1995) Comedy|Drama|Thriller 46 How to Make an American Quilt (1995) Drama|Romance 47 Seven (a.k.a. Se7en) (1995) Mystery|Thriller 48 Pocahontas (1995) Animation|Children|Drama|Musical|Romance 49 When Night Is Falling (1995) Drama|Romance 50 Usual Suspects, The (1995) Crime|Mystery|Thriller 51 Guardian Angel (1994) Action|Drama|Thriller 52 Mighty Aphrodite (1995) Comedy|Drama|Romance 53 Lamerica (1994) Adventure|Drama 54 Big Green, The (1995) Children|Comedy 55 Georgia (1995) Drama 56 Kids of the Round Table (1995) Adventure|Children|Comedy|Fantasy 57 Home for the Holidays (1995) Drama 58 Postman, The (Postino, Il) (1994) Comedy|Drama|Romance 59 Confessional, The (Confessionnal, Le) (1995) Drama|Mystery 60 Indian in the Cupboard, The (1995) Adventure|Children|Fantasy 61 Eye for an Eye (1996) Drama|Thriller 62 Mr. Holland's Opus (1995) Drama 63 Don't Be a Menace to South Central While Drinking Your Juice in the Hood (1996) Comedy|Crime 64 Two if by Sea (1996) Comedy|Romance 65 Bio-Dome (1996) Comedy 66 Lawnmower Man 2: Beyond Cyberspace (1996) Action|Sci-Fi|Thriller 67 Two Bits (1995) Drama 68 French Twist (Gazon maudit) (1995) Comedy|Romance 69 Friday (1995) Comedy 70 From Dusk Till Dawn (1996) Action|Comedy|Horror|Thriller 71 Fair Game (1995) Action 72 Kicking and Screaming (1995) Comedy|Drama 73 Misérables, Les (1995) Drama|War 74 Bed of Roses (1996) Drama|Romance 75 Big Bully (1996) Comedy|Drama 76 Screamers (1995) Action|Sci-Fi|Thriller 77 Nico Icon (1995) Documentary 78 Crossing Guard, The (1995) Action|Crime|Drama|Thriller 79 Juror, The (1996) Drama|Thriller 80 White Balloon, The (Badkonake sefid) (1995) Children|Drama 81 Things to Do in Denver When You're Dead (1995) Crime|Drama|Romance 82 Antonia's Line (Antonia) (1995) Comedy|Drama 83 Once Upon a Time... When We Were Colored (1995) Drama|Romance 84 Last Summer in the Hamptons (1995) Comedy|Drama 85 Angels and Insects (1995) Drama|Romance 86 White Squall (1996) Action|Adventure|Drama 87 Dunston Checks In (1996) Children|Comedy 88 Black Sheep (1996) Comedy 89 

In [0]:
#number of rows and columns
print(f"Number of rows: {movies_df.count()}")
print(f"Number of columns: {len(movies_df.columns)}")

Number of rows: 62423
Number of columns: 3


In [0]:
movies_df.schema

StructType([StructField('movieId', IntegerType(), True), StructField('title', StringType(), True), StructField('genres', StringType(), True)])

In [0]:
#summary
movies_df.describe().show()

+-------+------------------+--------------------+------------------+
|summary|           movieId|               title|            genres|
+-------+------------------+--------------------+------------------+
|  count|             62423|               62423|             62423|
|   mean|122220.38764557935|                NULL|              NULL|
| stddev| 63264.74484425336|                NULL|              NULL|
|    min|                 1|"""BLOW THE NIGHT...|(no genres listed)|
|    max|            209171|     줄탁동시 (2012)|           Western|
+-------+------------------+--------------------+------------------+



In [0]:
#dropping null values
movies_df = movies_df.na.drop()
print(f"Number of rows after dropping null values: {movies_df.count()}")

Number of rows after dropping null values: 62423


In [0]:
#remove duplicates
movies_df = movies_df.dropDuplicates()
print(f"Number of rows after removing duplicates: {movies_df.count()}")

Number of rows after removing duplicates: 62423


In [0]:
#Extract the year (if present) in the title column
movies_df = movies_df.withColumn("year", regexp_replace(col("title"), ".*\\((\\d{4})\\).*", "$1"))
movies_df.display()

movieId title genres year 109 Headless Body in Topless Bar (1995) Comedy|Drama|Thriller 1995 381 When a Man Loves a Woman (1994) Drama|Romance 1994 681 Coup de torchon (Clean Slate) (1981) Crime 1981 745 Wallace & Gromit: A Close Shave (1995) Animation|Children|Comedy 1995 1161 Tin Drum, The (Blechtrommel, Die) (1979) Drama|War 1979 1381 Grease 2 (1982) Comedy|Musical|Romance 1982 1410 Evening Star, The (1996) Comedy|Drama 1996 1678 Joy Luck Club, The (1993) Drama|Romance 1993 2230 Always Tell Your Wife (1914) Comedy 1914 2344 Runaway Train (1985) Action|Adventure|Drama|Thriller 1985 2519 House on Haunted Hill (1959) Drama|Horror|Thriller 1959 2782 Pit and the Pendulum (1961) Horror 1961 2904 Rain (1932) Drama 1932 3342 Birdy (1984) Drama|War 1984 3417 Crimson Pirate, The (1952) Adventure|Comedy 1952 3461 Lord of the Flies (1963) Adventure|Drama|Thriller 1963 3537 Where the Money Is (2000) Comedy|Drama 2000 3983 You Can Count on Me (2000) Drama|Romance 2000 4053 Double Take (2001) Action|Comedy 2001 4106 Extreme Prejudice (1987) Action|Crime|Drama|Thriller|Western 1987 4300 Bread and Roses (2000) Drama 2000 4821 Joy Ride (2001) Adventure|Thriller 2001 5083 Rare Birds (2001) Comedy|Drama 2001 5287 After Dark, My Sweet (1990) Crime|Drama|Mystery 1990 5491 Eddy Duchin Story, The (1956) Drama|Musical|Romance 1956 5580 Aspen Extreme (1993) Action 1993 5589 Indian Summer (1993) Comedy|Drama 1993 5598 Surf Ninjas (1993) Comedy 1993 6119 Santa Claus Is a Stinker (Le Père Noël est une ordure) (1982) Comedy 1982 6256 House with Laughing Windows, The (Casa dalle finestre che ridono, La) (1976) Horror|Mystery|Thriller 1976 6529 Strange Bedfellows (1965) Comedy 1965 6675 Far (2001) Drama 2001 7823 Demon Lover Diary (1980) Documentary 1980 8221 War of the Buttons (1994) Adventure|Children|Drama 1994 8253 Lupin III: The Castle Of Cagliostro (Rupan sansei: Kariosutoro no shiro) (1979) Action|Adventure|Animation|Comedy|Crime|Mystery 1979 8596 Revenge of the Pink Panther (1978) Comedy|Crime 1978 8849 Under the Cherry Moon (1986) Comedy|Drama|Musical|Romance 1986 25812 Scarlet Pimpernel, The (1934) Adventure|Comedy 1934 26227 House of Dark Shadows (1970) Drama|Horror|Romance 1970 26714 Across the Tracks (1991) Drama 1991 27646 Soldier's Girl (2003) Drama 2003 30659 Noel (2004) Drama 2004 31162 Life and Death of Peter Sellers, The (2004) Comedy|Drama 2004 32076 Godzilla vs. The Sea Monster (Gojira-Ebira-Mosura: Nankai no daiketto) (1966) Action|Adventure|Fantasy|Sci-Fi 1966 33201 Between Your Legs (Entre las piernas) (1999) Drama|Mystery|Romance|Thriller 1999 33426 9 Souls (Nain souruzu) (2003) Drama 2003 33808 Kings & Queen (Rois et reine) (2004) Comedy|Drama 2004 37949 Kwik Stop (2001) Comedy|Drama|Romance 2001 38304 No Direction Home: Bob Dylan (2005) Documentary 2005 42004 Transamerica (2005) Adventure|Comedy|Drama 2005 46574 OH in Ohio, The (2006) Comedy 2006 46967 Scoop (2006) Comedy|Fantasy|Mystery 2006 52356 Copying Beethoven (2006) Drama|Musical 2006 54116 First Snow (2006) Drama|Thriller 2006 56079 Smiley Face (2007) Comedy 2007 52 Mighty Aphrodite (1995) Comedy|Drama|Romance 1995 360 I Love Trouble (1994) Action|Comedy 1994 395 Desert Winds (1995) Drama|Fantasy|Romance 1995 405 Highlander III: The Sorcerer (a.k.a. Highlander: The Final Dimension) (1994) Action|Fantasy 1994 428 Bronx Tale, A (1993) Drama 1993 485 Last Action Hero (1993) Action|Adventure|Comedy|Fantasy 1993 656 Eddie (1996) Comedy 1996 675 Hostile Intentions (1994) Action|Drama|Thriller 1994 682 Tigrero: A Film That Was Never Made (1994) Documentary|Drama 1994 709 Oliver & Company (1988) Adventure|Animation|Children|Comedy|Musical 1988 808 Alaska (1996) Adventure|Children 1996 1102 American Strays (1996) Action 1996 1169 American Dream (1990) Documentary 1990 1722 Tomorrow Never Dies (1997) Action|Adventure|Thriller 1997 1777 Wedding Singer, The (1998) Comedy|Romance 1998 1872 Go Now (1995) Drama 1995 1901 Dear Jesse (1997) Documentary 1997 2635 Mummy's Curse, The (1944)

In [0]:
#remove the informations inside the parenthesis
movies_df = movies_df.withColumn("title", regexp_replace(col("title"), "\\([^)]*\\)", ""))
movies_df.display()

movieId title genres year 109 Headless Body in Topless Bar Comedy|Drama|Thriller 1995 381 When a Man Loves a Woman Drama|Romance 1994 681 Coup de torchon Crime 1981 745 Wallace & Gromit: A Close Shave Animation|Children|Comedy 1995 1161 Tin Drum, The Drama|War 1979 1381 Grease 2 Comedy|Musical|Romance 1982 1410 Evening Star, The Comedy|Drama 1996 1678 Joy Luck Club, The Drama|Romance 1993 2230 Always Tell Your Wife Comedy 1914 2344 Runaway Train Action|Adventure|Drama|Thriller 1985 2519 House on Haunted Hill Drama|Horror|Thriller 1959 2782 Pit and the Pendulum Horror 1961 2904 Rain Drama 1932 3342 Birdy Drama|War 1984 3417 Crimson Pirate, The Adventure|Comedy 1952 3461 Lord of the Flies Adventure|Drama|Thriller 1963 3537 Where the Money Is Comedy|Drama 2000 3983 You Can Count on Me Drama|Romance 2000 4053 Double Take Action|Comedy 2001 4106 Extreme Prejudice Action|Crime|Drama|Thriller|Western 1987 4300 Bread and Roses Drama 2000 4821 Joy Ride Adventure|Thriller 2001 5083 Rare Birds Comedy|Drama 2001 5287 After Dark, My Sweet Crime|Drama|Mystery 1990 5491 Eddy Duchin Story, The Drama|Musical|Romance 1956 5580 Aspen Extreme Action 1993 5589 Indian Summer Comedy|Drama 1993 5598 Surf Ninjas Comedy 1993 6119 Santa Claus Is a Stinker Comedy 1982 6256 House with Laughing Windows, The Horror|Mystery|Thriller 1976 6529 Strange Bedfellows Comedy 1965 6675 Far Drama 2001 7823 Demon Lover Diary Documentary 1980 8221 War of the Buttons Adventure|Children|Drama 1994 8253 Lupin III: The Castle Of Cagliostro Action|Adventure|Animation|Comedy|Crime|Mystery 1979 8596 Revenge of the Pink Panther Comedy|Crime 1978 8849 Under the Cherry Moon Comedy|Drama|Musical|Romance 1986 25812 Scarlet Pimpernel, The Adventure|Comedy 1934 26227 House of Dark Shadows Drama|Horror|Romance 1970 26714 Across the Tracks Drama 1991 27646 Soldier's Girl Drama 2003 30659 Noel Drama 2004 31162 Life and Death of Peter Sellers, The Comedy|Drama 2004 32076 Godzilla vs. The Sea Monster Action|Adventure|Fantasy|Sci-Fi 1966 33201 Between Your Legs Drama|Mystery|Romance|Thriller 1999 33426 9 Souls Drama 2003 33808 Kings & Queen Comedy|Drama 2004 37949 Kwik Stop Comedy|Drama|Romance 2001 38304 No Direction Home: Bob Dylan Documentary 2005 42004 Transamerica Adventure|Comedy|Drama 2005 46574 OH in Ohio, The Comedy 2006 46967 Scoop Comedy|Fantasy|Mystery 2006 52356 Copying Beethoven Drama|Musical 2006 54116 First Snow Drama|Thriller 2006 56079 Smiley Face Comedy 2007 52 Mighty Aphrodite Comedy|Drama|Romance 1995 360 I Love Trouble Action|Comedy 1994 395 Desert Winds Drama|Fantasy|Romance 1995 405 Highlander III: The Sorcerer Action|Fantasy 1994 428 Bronx Tale, A Drama 1993 485 Last Action Hero Action|Adventure|Comedy|Fantasy 1993 656 Eddie Comedy 1996 675 Hostile Intentions Action|Drama|Thriller 1994 682 Tigrero: A Film That Was Never Made Documentary|Drama 1994 709 Oliver & Company Adventure|Animation|Children|Comedy|Musical 1988 808 Alaska Adventure|Children 1996 1102 American Strays Action 1996 1169 American Dream Documentary 1990 1722 Tomorrow Never Dies Action|Adventure|Thriller 1997 1777 Wedding Singer, The Comedy|Romance 1998 1872 Go Now Drama 1995 1901 Dear Jesse Documentary 1997 2635 Mummy's Curse, The Horror 1944 2720 Inspector Gadget Action|Adventure|Children|Comedy 1999 2855 Nightmares Horror 1983 2943 Indochine Drama|Romance 1992 3279 Knockout Action|Drama 2000 3383 Big Fella Drama|Musical 1937 3886 Steal This Movie! Drama 2000 4060 Love Field Drama 1992 4150 Signs & Wonders Drama 2001 4227 Brothers, The Comedy|Drama 2001 4555 Torch Song Trilogy Comedy|Drama|Romance 1988 4863 Female Trouble Comedy|Crime 1975 4909 Incredible Shrinking Woman, The Comedy|Sci-Fi 1981 4918 Young Lions, The Drama|War 1958 5000 Medium Cool Drama|Romance 1969 5345 Triumph of the Spirit Drama 1989 5620 Sweet Home Alabama Comedy|Romance 2002 5899 Zulu Action|Drama|War 1964 6084 Honkytonk Man Comedy|Drama 1982 6162 Gerry Adventure|Drama 2002 6254 Awful Truth, The Comedy|Romance 1937 6317 Carto

In [0]:
#Rearrange the title

# Define the rearrange function
def rearrange_movie_title(title):
    """
    Rearrange titles of the format 'Title, The' to 'The Title'.
    """
    if title is not None:
        title = title.strip()
        return re.sub(r"^(.*?), (The|A|An)$", r"\2 \1", title).strip()
    return title  # Handle None values

# Register the function as a UDF
rearrange_udf = udf(rearrange_movie_title, StringType())

# Apply to the Spark DataFrame
movies_df = movies_df.withColumn("title", rearrange_udf(col("title")))

# Show the updated DataFrame
movies_df.display()


movieId title genres year 109 Headless Body in Topless Bar Comedy|Drama|Thriller 1995 381 When a Man Loves a Woman Drama|Romance 1994 681 Coup de torchon Crime 1981 745 Wallace & Gromit: A Close Shave Animation|Children|Comedy 1995 1161 The Tin Drum Drama|War 1979 1381 Grease 2 Comedy|Musical|Romance 1982 1410 The Evening Star Comedy|Drama 1996 1678 The Joy Luck Club Drama|Romance 1993 2230 Always Tell Your Wife Comedy 1914 2344 Runaway Train Action|Adventure|Drama|Thriller 1985 2519 House on Haunted Hill Drama|Horror|Thriller 1959 2782 Pit and the Pendulum Horror 1961 2904 Rain Drama 1932 3342 Birdy Drama|War 1984 3417 The Crimson Pirate Adventure|Comedy 1952 3461 Lord of the Flies Adventure|Drama|Thriller 1963 3537 Where the Money Is Comedy|Drama 2000 3983 You Can Count on Me Drama|Romance 2000 4053 Double Take Action|Comedy 2001 4106 Extreme Prejudice Action|Crime|Drama|Thriller|Western 1987 4300 Bread and Roses Drama 2000 4821 Joy Ride Adventure|Thriller 2001 5083 Rare Birds Comedy|Drama 2001 5287 After Dark, My Sweet Crime|Drama|Mystery 1990 5491 The Eddy Duchin Story Drama|Musical|Romance 1956 5580 Aspen Extreme Action 1993 5589 Indian Summer Comedy|Drama 1993 5598 Surf Ninjas Comedy 1993 6119 Santa Claus Is a Stinker Comedy 1982 6256 The House with Laughing Windows Horror|Mystery|Thriller 1976 6529 Strange Bedfellows Comedy 1965 6675 Far Drama 2001 7823 Demon Lover Diary Documentary 1980 8221 War of the Buttons Adventure|Children|Drama 1994 8253 Lupin III: The Castle Of Cagliostro Action|Adventure|Animation|Comedy|Crime|Mystery 1979 8596 Revenge of the Pink Panther Comedy|Crime 1978 8849 Under the Cherry Moon Comedy|Drama|Musical|Romance 1986 25812 The Scarlet Pimpernel Adventure|Comedy 1934 26227 House of Dark Shadows Drama|Horror|Romance 1970 26714 Across the Tracks Drama 1991 27646 Soldier's Girl Drama 2003 30659 Noel Drama 2004 31162 The Life and Death of Peter Sellers Comedy|Drama 2004 32076 Godzilla vs. The Sea Monster Action|Adventure|Fantasy|Sci-Fi 1966 33201 Between Your Legs Drama|Mystery|Romance|Thriller 1999 33426 9 Souls Drama 2003 33808 Kings & Queen Comedy|Drama 2004 37949 Kwik Stop Comedy|Drama|Romance 2001 38304 No Direction Home: Bob Dylan Documentary 2005 42004 Transamerica Adventure|Comedy|Drama 2005 46574 The OH in Ohio Comedy 2006 46967 Scoop Comedy|Fantasy|Mystery 2006 52356 Copying Beethoven Drama|Musical 2006 54116 First Snow Drama|Thriller 2006 56079 Smiley Face Comedy 2007 52 Mighty Aphrodite Comedy|Drama|Romance 1995 360 I Love Trouble Action|Comedy 1994 395 Desert Winds Drama|Fantasy|Romance 1995 405 Highlander III: The Sorcerer Action|Fantasy 1994 428 A Bronx Tale Drama 1993 485 Last Action Hero Action|Adventure|Comedy|Fantasy 1993 656 Eddie Comedy 1996 675 Hostile Intentions Action|Drama|Thriller 1994 682 Tigrero: A Film That Was Never Made Documentary|Drama 1994 709 Oliver & Company Adventure|Animation|Children|Comedy|Musical 1988 808 Alaska Adventure|Children 1996 1102 American Strays Action 1996 1169 American Dream Documentary 1990 1722 Tomorrow Never Dies Action|Adventure|Thriller 1997 1777 The Wedding Singer Comedy|Romance 1998 1872 Go Now Drama 1995 1901 Dear Jesse Documentary 1997 2635 The Mummy's Curse Horror 1944 2720 Inspector Gadget Action|Adventure|Children|Comedy 1999 2855 Nightmares Horror 1983 2943 Indochine Drama|Romance 1992 3279 Knockout Action|Drama 2000 3383 Big Fella Drama|Musical 1937 3886 Steal This Movie! Drama 2000 4060 Love Field Drama 1992 4150 Signs & Wonders Drama 2001 4227 The Brothers Comedy|Drama 2001 4555 Torch Song Trilogy Comedy|Drama|Romance 1988 4863 Female Trouble Comedy|Crime 1975 4909 The Incredible Shrinking Woman Comedy|Sci-Fi 1981 4918 The Young Lions Drama|War 1958 5000 Medium Cool Drama|Romance 1969 5345 Triumph of the Spirit Drama 1989 5620 Sweet Home Alabama Comedy|Romance 2002 5899 Zulu Action|Drama|War 1964 6084 Honkytonk Man Comedy|Drama 1982 6162 Gerry Adventure|Drama 2002 6254 The Awful Truth Comedy|Romance 1937 6317 Cartouche Action|Adve

In [0]:
movies_df.repartition(1).write.format('csv')\
    .mode('overwrite')\
    .option("header", "true")\
    .option("path", "abfss://silver@movierecommendation2025.dfs.core.windows.net/movies")\
    .save()